#### Import packages and data

In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import time

from glob import glob
from functools import reduce
import matplotlib.pyplot as plt
%matplotlib inline

from scipy import stats 

In [2]:
business=pd.read_csv("/Users/Zeeshan/Downloads/yelp_business_85001-85099.csv", sep=',')
demographics=pd.read_csv("/Users/Zeeshan/Downloads/Census.csv", sep=',')

In [3]:
business.head(2)

business_id                            name  neighborhood  \
0  rDMptJYWtnMhpQu_rRXHng                    "McDonald's"           NaN   
1  1WBkAuQg81kokZIPMpn9Zg  "Charr An American Burger Bar"           NaN   

                           address     city state  postal_code  latitude  \
0           "719 E Thunderbird Rd"  Phoenix    AZ        85022  33.60707   
1  "777 E Thunderbird Rd, Ste 107"  Phoenix    AZ        85022  33.60731   

    longitude  stars  review_count  is_open                     categories  
0 -112.064382    1.0            10        1  Fast Food;Burgers;Restaurants  
1 -112.063404    3.0           232        1            Burgers;Restaurants

#### Generate new column for single category

In [4]:
business['cat'] = "NA"

#### Generate Dummy Variable Columns

In [5]:
list_dv = ['Fast Food','Bars','Gluten-Free','Vegetarian','Vegan','Pizza']

In [6]:
for i in list_dv: 
    business[i] = business['categories'].str.contains(i, regex=False)

In [7]:
business.head(2)

business_id                            name  neighborhood  \
0  rDMptJYWtnMhpQu_rRXHng                    "McDonald's"           NaN   
1  1WBkAuQg81kokZIPMpn9Zg  "Charr An American Burger Bar"           NaN   

                           address     city state  postal_code  latitude  \
0           "719 E Thunderbird Rd"  Phoenix    AZ        85022  33.60707   
1  "777 E Thunderbird Rd, Ste 107"  Phoenix    AZ        85022  33.60731   

    longitude  stars  review_count  is_open                     categories  \
0 -112.064382    1.0            10        1  Fast Food;Burgers;Restaurants   
1 -112.063404    3.0           232        1            Burgers;Restaurants   

  cat  Fast Food   Bars  Gluten-Free  Vegetarian  Vegan  Pizza  
0  NA       True  False        False       False  False  False  
1  NA      False  False        False       False  False  False

#### Filter by restaurants

In [8]:
business['temp'] = "0"
business['temp'] = business['categories'].str.contains('Restaurant', regex=False)
business = business[business.temp == True]
business['temp'].value_counts()

True    3652
Name: temp, dtype: int64

#### Categorize a restaurant based on categories

In [9]:
list_cat = ['Nightlife','Music Venues','Venues & Event Spaces','Arts & Entertainment','Grocery',
            
            #######
            
            #generic categories go first
            'Comfort Food',
            'Bars',
            'Fast Food',
            'Breakfast & Brunch',
            'Desserts',           
            'Cafes','Bakeries','Delis','Cafeteria',
            'American (Traditional)',
            'American (New)',
            'Seafood',
            'Buffets',
            'Gluten-Free','Vegetarian', 'Vegan',
            'Cheesesteaks','Chicken',
            'Hot Dogs',
            
            #Filter through American food
            'Sandwiches','Burgers','Sports Bars','Barbeque','Steakhouses',
            #Filter through central American food
            'Latin America','Mexican','Tex-Mex','Peruvian','Salvadoran',
            #Filter through Mediterranean food
            'Mediterranean','Greek',
            #Filter through Asian Food
            'Chinese','Asian Fusion','Thai','Vietnamese','Japanese','Sushi',
            'Korean',
            #Filter through Middle East
            'Middle Eastern',
            
            #Filter through pizza and Italian
            'Pizza','Italian',
            #Filter through Carribean
            'Carribean','Caribbean','Cajun','Cuban',
            #Filter through European 
            'Modern European','French',
            'Russian','Ukranian','Polish','Uzbek','Afghan',
            'German','Bavarian',
            'Spanish',
            #Filter through African
            'African','Ethiopian',
            #Filter throuh Indian
            'Indian',#'Pakistani',
                     
            #Filter through Southern
            'Southern','Diners','Soul Food',
            #Filter through bar restaurants
            'Sports Bar','Wine Bars','Gastropub','Cocktail Bars','Dive Bar',
            #Filter through misc.
            'Coffee & Tea','Juice Bars & Smoothies','Ice Cream & Frozen Yogurt',
            'Bagels', 'Donuts',
            'Fish & Chips','Kosher','Pretzels',
            'Hawaiian', 
            
            ########
            
            #Label things that are not restaurants
            
            'Festival','Food Trucks','Event Planning & Services','Grocery', 
            'Food Delivery Services','Shopping','Active Life', 'Party & Event Planning',
            'Health Markets','Convenience Stores', 'Arcades','Professional Services',
            'Home & Garden','Dance Clubs', 'Wholesalers','Restaurant Supplies',
            'Automotive','Furniture Stores', 'Health & Medical','Gas Stations',
            'Kitchen & Bath','Beauty & Spas', 'Home Services','Appliances','Day Spas',
            'Personal Chefs','Caterers', 'Fashion','Food Court','Veterinarians'
            
             ]

In [10]:
for i in list_cat: 
    business['temp'] = "0"
    business['temp'] = business['categories'].str.contains(i, regex=False)
    business['cat'] = np.where(business['temp'] == True, i, business['cat'])

In [11]:
business['cat'].value_counts()

Mexican                      513
Sandwiches                   268
Burgers                      264
Italian                      217
Pizza                        195
Chinese                      164
Caterers                     117
American (Traditional)       115
American (New)                94
Coffee & Tea                  92
Sports Bar                    92
Sushi                         75
Tex-Mex                       61
Diners                        60
Greek                         59
Fast Food                     53
Food Trucks                   52
Barbeque                      52
Wine Bars                     50
Ice Cream & Frozen Yogurt     46
Chicken                       44
Thai                          43
Cocktail Bars                 43
Steakhouses                   40
Vietnamese                    38
Indian                        34
Juice Bars & Smoothies        34
Asian Fusion                  32
Japanese                      31
Bagels                        27
          

#### Remove non-restaurant categories that still remain

In [12]:
list_drop = ['Appliances','Home Services','Festival','Health & Medical',
             'Gas Stations','Day Spas','Restaurant Supplies',
             'Personal Chefs','Veterinarians','Arts & Entertainment',
             'Kitchen & Bath','Nightlife','Furniture Stores','Beauty & Spas',
             'Arcades','Dance Clubs','Party & Event Planning',
             'Convenience Stores','Caterers','Food Trucks','Active Life',
             'Food Delivery Services','Health Markets','Shopping','Grocery',
             'Event Planning & Services','Fashion'
            ]

In [13]:
for i in list_drop:
    business = business.loc[business['cat'] != i]

In [14]:
business.shape[0]

3318

In [15]:
pd.set_option('display.max_row', 100)
business['cat'].value_counts()

Mexican                      513
Sandwiches                   268
Burgers                      264
Italian                      217
Pizza                        195
Chinese                      164
American (Traditional)       115
American (New)                94
Coffee & Tea                  92
Sports Bar                    92
Sushi                         75
Tex-Mex                       61
Diners                        60
Greek                         59
Fast Food                     53
Barbeque                      52
Wine Bars                     50
Ice Cream & Frozen Yogurt     46
Chicken                       44
Cocktail Bars                 43
Thai                          43
Steakhouses                   40
Vietnamese                    38
Juice Bars & Smoothies        34
Indian                        34
Asian Fusion                  32
Japanese                      31
Bagels                        27
Middle Eastern                26
Mediterranean                 26
NA        

#### Categorize a restaurant by its name

In [16]:
business['temp'] = business['name'].str.contains('Burger King', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Burger', business['cat'])

In [17]:
business['temp'] = business['name'].str.contains('McDonalds', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Burger', business['cat'])

In [18]:
business['temp'] = business['name'].str.contains('Dairy Queen', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Ice Cream & Frozen Yogurt', business['cat'])

In [19]:
business['temp'] = business['name'].str.contains('Noodles & Company', regex=False)
business['cat'] = np.where(business['temp'] == True, 'American (New)', business['cat'])

In [20]:
business['temp'] = business['name'].str.contains('The Loaded Potato', regex=False)
business['cat'] = np.where(business['temp'] == True, 'American (New)', business['cat'])

In [21]:
business['temp'] = business['name'].str.contains('Food Court', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Food Court', business['cat'])

In [22]:
business['temp'] = business['name'].str.contains('Sonic', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Ice Cream & Frozen Yogurt', business['cat'])

In [23]:
business['temp'] = business['name'].str.contains('Mighty Mikes', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Burger', business['cat'])

In [24]:
business['temp'] = business['name'].str.contains('Salad', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Salad', business['cat'])

In [25]:
business['temp'] = business['name'].str.contains('Pizza', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Pizza', business['cat'])

In [26]:
business['temp'] = business['name'].str.contains('pizza', regex=False)
business['cat'] = np.where(business['temp'] == True, 'pizza', business['cat'])

In [27]:
business['temp'] = business['name'].str.contains('Taco', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Mexican', business['cat'])

In [28]:
business['temp'] = business['name'].str.contains('taco', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Mexican', business['cat'])

In [29]:
business['temp'] = business['name'].str.contains('Carl', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Burgers', business['cat'])

In [30]:
business['temp'] = business['name'].str.contains('Red Robin', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Burgers', business['cat'])

In [31]:
business['temp'] = business['name'].str.contains(r'(?=.*Jack)(?=.*Box)',regex=True)
business['cat'] = np.where(business['temp'] == True, 'Burgers', business['cat'])

In [32]:
business['temp'] = business['name'].str.contains(r'(?=.*Jack)(?=.*box)',regex=True)
business['cat'] = np.where(business['temp'] == True, 'Burgers', business['cat'])

In [33]:
business['temp'] = business['name'].str.contains('Chicken', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Chicken', business['cat'])

In [34]:
business['temp'] = business['name'].str.contains('Fish', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Seafood', business['cat'])

In [35]:
business['temp'] = business['name'].str.contains('Fish & Chips', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Fish & Chips', business['cat'])

In [36]:
business['temp'] = business['name'].str.contains('Wong', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Chinese', business['cat'])

In [37]:
business['temp'] = business['name'].str.contains('Grill', regex=False)
business['cat'] = np.where(business['temp'] == True, 'American (New)', business['cat'])

In [38]:
business['temp'] = business['name'].str.contains('Cafe', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Cafe', business['cat'])

In [39]:
business['temp'] = business['name'].str.contains('Deli', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Deli', business['cat'])

In [40]:
business['temp'] = business['name'].str.contains('Pretzels', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Pretzels', business['cat'])

In [41]:
business['temp'] = business['name'].str.contains('Nueva', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Mexican', business['cat'])

In [42]:
business['temp'] = business['name'].str.contains('Pueblo', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Mexican', business['cat'])

In [43]:
business['temp'] = business['name'].str.contains('Salsita', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Mexican', business['cat'])

In [44]:
pd.set_option('display.max_row', 100)
business['cat'].value_counts()

Mexican                      490
American (New)               323
Pizza                        279
Burgers                      259
Sandwiches                   226
Chinese                      168
Cafe                         165
Italian                      120
Coffee & Tea                  71
Sushi                         67
Chicken                       60
American (Traditional)        59
Ice Cream & Frozen Yogurt     58
Diners                        51
Barbeque                      49
Greek                         48
Sports Bar                    47
Thai                          42
Cocktail Bars                 41
Wine Bars                     40
Burger                        40
Deli                          38
Vietnamese                    37
Steakhouses                   37
Indian                        29
Japanese                      27
Juice Bars & Smoothies        27
Asian Fusion                  26
Seafood                       22
Bagels                        20
Hot Dogs  

#### Consolidate categories

In [45]:
business['temp'] = business['cat'].str.contains('Bavarian', regex=False)
business['cat'] = np.where(business['temp'] == True, 'German', business['cat'])

In [46]:
business['temp'] = business['cat'].str.contains('Salvadoran', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Latin America', business['cat'])

In [47]:
business['temp'] = business['cat'].str.contains('Peruvian', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Latin America', business['cat'])

In [48]:
business['temp'] = business['cat'].str.contains('Ethiopian', regex=False)
business['cat'] = np.where(business['temp'] == True, 'African', business['cat'])

In [49]:
business['temp'] = business['cat'].str.contains('Cheesesteaks', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Sandwiches', business['cat'])

In [50]:
business['temp'] = business['cat'].str.contains('pizza', regex=False)
business['cat'] = np.where(business['temp'] == True, 'Pizza', business['cat'])

In [51]:
business['cat'].value_counts()

Mexican                      490
American (New)               323
Pizza                        281
Burgers                      259
Sandwiches                   227
Chinese                      168
Cafe                         165
Italian                      120
Coffee & Tea                  71
Sushi                         67
Chicken                       60
American (Traditional)        59
Ice Cream & Frozen Yogurt     58
Diners                        51
Barbeque                      49
Greek                         48
Sports Bar                    47
Thai                          42
Cocktail Bars                 41
Burger                        40
Wine Bars                     40
Deli                          38
Vietnamese                    37
Steakhouses                   37
Indian                        29
Juice Bars & Smoothies        27
Japanese                      27
Asian Fusion                  26
Seafood                       22
Bagels                        20
Hot Dogs  

#### National chains (https://www.restaurantbusinessonline.com/top-500-chains)

In [52]:
business['chain'] = False
business['chain'] = business.groupby(['name']).transform('count')

In [53]:
business['chain'] = np.where(business['chain'] > 1, True, False)

In [54]:
business['Fast Food'].value_counts()

False    2745
True      573
Name: Fast Food, dtype: int64

In [55]:
business['Bars'].value_counts()

False    2801
True      517
Name: Bars, dtype: int64

In [56]:
business['Gluten-Free'].value_counts()

False    3269
True       49
Name: Gluten-Free, dtype: int64

In [57]:
business['Vegetarian'].value_counts()

False    3253
True       65
Name: Vegetarian, dtype: int64

In [58]:
business['Vegan'].value_counts()

False    3284
True       34
Name: Vegan, dtype: int64

In [59]:
business['Pizza'].value_counts()

False    2933
True      385
Name: Pizza, dtype: int64

In [60]:
business['chain'].value_counts()

False    2087
True     1231
Name: chain, dtype: int64

In [61]:
business.head(20)
business.to_csv('/Users/Zeeshan/Downloads/business.csv',sep=',',index= False)

#### Use the code below to interrogate categories

In [62]:
i = False #write in what category you are interested in

In [63]:
bizzy = business.loc[business['chain']==i]
pd.set_option('display.max_row', 100)
bizzy['name'].value_counts() ==1

"Super Oscars"                                True
"El Entronke Mexican Food"                    True
"Pei Wei Asian Diner"                         True
"Matador Restaurant"                          True
"ASAP California Pizza Kitchen"               True
"Turk's Fish and Chips"                       True
"Ippei"                                       True
"MidiCi The Neapolitan Pizza Company"         True
"Garcia's Las Avenidas"                       True
"Panaderia Y Tortilleria"                     True
"Carmella's Italian Kitchen and Bar"          True
"Cycle"                                       True
"Duza's Kitchen"                              True
"El Portal"                                   True
"Jb's"                                        True
"Wang Express"                                True
"Canyon 49 Grill"                             True
"Great Wall Cuisine"                          True
"Fenix Eatery & Bar"                          True
"Famous Famiglia Pizzeria"     

In [64]:
bizzy.head(20)

business_id                              name  neighborhood  \
1   1WBkAuQg81kokZIPMpn9Zg    "Charr An American Burger Bar"           NaN   
5   5XejqzaFmtkZMstJS5Iy-w                     "D'Lish Cafe"           NaN   
7   M3uV9Y3EDSpy9d4YwyNSAQ                       "Yakiramen"           NaN   
8   U1ZVgF-kfkvv_rcoe0RglQ                     "Pho Noodles"           NaN   
9   FfI9FOaQqzUxixw6_glt3Q               "Affinito's Bistro"           NaN   
12  _eKvk2GoGKb3CoYolHgRlg  "Fresko A Mediterranean Kitchen"           NaN   
14  rSCevr5tQJTxPzMIq3n5Gw             "Yoshi's Asian Grill"           NaN   
15  to2cGMKdaw7ZHbXMzpfhlA        "Filiberto's Mexican Rest"           NaN   
16  X2oxkKB-wlu8xV0P8fbfiQ                    "Mo's Chicken"           NaN   
18  frCxZS7lPhEnQRJ3UY6m7A                    "La Santisima"           NaN   
19  l0WauZ92kRg9bu2oxHj4TQ     "Aiello's East Coast Italian"           NaN   
20  Yar8jR2a1XA2JuRKfmNDcw                "Palms Restaurant"           NaN   
21  qVQGfHphxolps16v6g5X-g   "Belfiore's Italian Ristorante"           NaN   
23  TolwZ3L28or4E8SVTZUf6Q                 "Spinato's Pizza"           NaN   
25  9KzLFQrA_tSBGVDNeZrB8Q    "Nick and Willy's Take & Bake"           NaN   
26  Ld2hhA3q3cdkptwS1fsYEg                    "Yogi's Grill"           NaN   
27  r0byBoB7y_IH8uicEvyCqQ                  "Rack Shack BBQ"           NaN   
29  aRRV_ZbRiD65SIi7vAY-iA                   "Zest of India"           NaN   
30  yX0pOWG_Be9TjGnm0aihVA                   "Modern  Grove"           NaN   
31  WaTXG26xbOGffSscvyr-wQ   "Spasso Pizza & Mozzarella Bar"           NaN   

                            address     city state  postal_code   latitude  \
1   "777 E Thunderbird Rd, Ste 107"  Phoenix    AZ        85022  33.607310   
5                 "503 W Thomas Rd"  Phoenix    AZ        85013  33.480301   
7                "10605 N 43rd Ave"  Phoenix    AZ        85029  33.582363   
8                  "3417 N 7th Ave"  Phoenix    AZ        85013  33.488760   
9    "3655 W Anthem Way, Ste C-137"  Phoenix    AZ        85086  33.864964   
12               "5033 E Elliot Rd"  Phoenix    AZ        85044  33.347893   
14         "3800 E Sky Harbor Blvd"  Phoenix    AZ        85034  33.435621   
15             "3218 E Mcdowell Rd"  Phoenix    AZ        85008  33.466011   
16               "3505 W Thomas Rd"  Phoenix    AZ        85019  33.480049   
18                 "1919 N 16th St"  Phoenix    AZ        85006  33.469201   
19  "777 E Thunderbird Rd, Ste 100"  Phoenix    AZ        85022  33.607105   
20          "3502 West Greenway Rd"  Phoenix    AZ        85053  33.625952   
21          "15842 N Cave Creek Rd"  Phoenix    AZ        85032  33.630857   
23    "1219 E Glendale Ave, Ste 14"  Phoenix    AZ        85020  33.537871   
25                 "13216 N 7th St"  Phoenix    AZ        85022  33.606055   
26         "2450 W Happy Valley Rd"  Phoenix    AZ        85085  33.714506   
27        "1019 E Indian School Rd"  Phoenix    AZ        85014  33.494234   
29   "3202 E Greenway Rd, Ste 1617"  Phoenix    AZ        85032  33.626418   
30    "15530 N Tatum Blvd, Ste 160"  Phoenix    AZ        85032  33.627460   
31       "4743 N 20th St, Ste A22A"  Phoenix    AZ        85016  33.448377   

     longitude  stars  ...    \
1  -112.063404    3.0  ...     
5  -112.080586    4.0  ...     
7  -112.149884    4.0  ...     
8  -112.082402    4.5  ...     
9  -112.138820    3.0  ...     
12 -111.976822    4.5  ...     
14 -112.009546    2.5  ...     
15 -112.012334    3.0  ...     
16 -112.134702    3.0  ...     
18 -112.047393    4.0  ...     
19 -112.063427    4.0  ...     
20 -112.134338    5.0  ...     
21 -112.030924    3.5  ...     
23 -112.055161    4.0  ...     
25 -112.066400    3.5  ...     
26 -112.112238    4.0  ...     
27 -112.059741    3.0  ...     
29 -112.013246    1.0  ...     
30 -111.978456    3.0  ...     
31 -112.074037    3.5  ...     

                                           categories           

In [65]:
business_attributes=pd.read_csv('/Users/Zeeshan/Downloads/yelp_business_attributes.csv')
business_hours=pd.read_csv('/Users/Zeeshan/Downloads/yelp_business_hours.csv')

In [66]:
def basic_details(df):
    print('Row:{}, columns:{}'.format(df.shape[0],df.shape[1]))
    k = pd.DataFrame()
    k['number of Unique value'] = df.nunique()
    k['Number of missing value'] = df.isnull().sum()
    k['Data type'] = df.dtypes
    return k

In [67]:
cols_v = list(business_hours.columns.values)[1:]

for i in range(len(cols_v)):
    #print(cols_v[i])
    business_hours[cols_v[i]].replace('None', np.nan, inplace=True)

#business_hours.nunique()

In [68]:
#basic_details(business_hours)

In [69]:




## function for get time_range from string
def get_time_range(s):
    if isinstance(s, str):
        t1, t2 = s.split('-')
        h1, m1 = map(int, t1.split(':'))
        h2, m2 = map(int, t2.split(':'))
        m1, m2 = m1/60, m2/60
        t1, t2 = h1+m1, h2+m2
        if t2 < t1:
            d = t2+24-t1
        else:
            d = t2-t1
        return t1, t2, d
    else:
        return None, None, None

## Prepare start/finish/delta features for every weekday
bh_colnames = business_hours.columns
for c in bh_colnames[1:]:
    business_hours['{0}_s'.format(c[:2])] = business_hours[c].apply(lambda d: get_time_range(d)[0])
    business_hours['{0}_f'.format(c[:2])] = business_hours[c].apply(lambda d: get_time_range(d)[1])
    business_hours['{0}_d'.format(c[:2])] = business_hours[c].apply(lambda d: get_time_range(d)[2])
# business_hours = business_hours.drop(bh_colnames[1:], axis=1)
business_hours


# # define weekday vs weekend categories
# weekdays = ['mo', 'tu', 'we', 'th']
# fridays = ['fr']
# weekends = ['sa', 'su']

# ## define new_cols
# bh_newcols = ['business_id']
# for wg_name, wg in zip(['weekdays', 'fridays', 'weekends'], [weekdays, fridays, weekends]):
#     for f in ['s', 'f', 'd']:
#         cols = list(map(lambda d: '{0}_{1}'.format(d,f), wg))
#         bh_newcols.append('{0}_{1}'.format(wg_name, f))
#         b_hours['{0}_{1}'.format(wg_name, f)] = b_hours.loc[:, cols].median(axis=1)

# b_hours.loc[:, bh_newcols].head(30)

business_hours['monday']=np.where(business_hours.monday.notnull(),1,0)
business_hours['tuesday']=np.where(business_hours.tuesday.notnull(),1,0)
business_hours['wednesday']=np.where(business_hours.wednesday.notnull(),1,0)
business_hours['thursday']=np.where(business_hours.thursday.notnull(),1,0)
business_hours['friday']=np.where(business_hours.friday.notnull(),1,0)
business_hours['saturday']=np.where(business_hours.saturday.notnull(),1,0)
business_hours['sunday']=np.where(business_hours.sunday.notnull(),1,0)



business_hours['open_weekdays'] = np.where((business_hours['monday']==1) & 
                                           (business_hours['tuesday']==1) & 
                                           (business_hours['wednesday']==1) & 
                                           (business_hours['thursday']==1),1,0)
business_hours['open_fridays']=np.where(business_hours['friday']==1,1,0)
business_hours['open_weekends']=np.where((business_hours['saturday']==1)|
                                         (business_hours['sunday']==1),1,0)

business_hours

#break categories down further
#breakfast: 5 a.m. to 10:30 a.m.
#lunch: 11 a.m. to 3:30 p.m.
#dinner: 4 p.m. to 9:30 p.m.
#late_night: 10 p.m. to 4:30 a.m.

business_hours['weekday_breakfast']=np.where(
    (business_hours['mo_s']> 4.5)&(business_hours['mo_s']<10.5)|
    (business_hours['tu_s']> 4.5)&(business_hours['tu_s']<10.5)|
    (business_hours['we_s']> 4.5)&(business_hours['we_s']<10.5)|
    (business_hours['th_s']> 4.5)&(business_hours['th_s']<10.5)|
    (business_hours['fr_s']> 4.5)&(business_hours['fr_s']<10.5),1,0)

business_hours['weekend_breakfast']=np.where(
    (business_hours['sa_s']> 4.5)&(business_hours['sa_s']<10.5)|
    (business_hours['su_s']> 4.5)&(business_hours['su_s']<10.5),1,0)

business_hours['weekday_lunch']=np.where(
    (business_hours['mo_s']< 10.5)&(business_hours['mo_f']>15.5)|
    (business_hours['tu_s']< 10.5)&(business_hours['tu_f']>15.5)|
    (business_hours['we_s']< 10.5)&(business_hours['we_f']>15.5)|
    (business_hours['th_s']< 10.5)&(business_hours['th_f']>15.5)|
    (business_hours['fr_s']< 10.5)&(business_hours['fr_f']>15.5),1,0)

business_hours['weekend_lunch']=np.where(
    (business_hours['sa_s']< 11)&(business_hours['sa_f']>15.5)|
    (business_hours['su_s']< 11)&(business_hours['su_f']>15.5),1,0)

business_hours['weekday_dinner']=np.where(
    (business_hours['mo_s']< 15.5)&(business_hours['mo_f']>20)|
    (business_hours['tu_s']< 15.5)&(business_hours['tu_f']>20)|
    (business_hours['we_s']< 15.5)&(business_hours['we_f']>20)|
    (business_hours['th_s']< 15.5)&(business_hours['th_f']>20)|
    (business_hours['fr_s']< 15.5)&(business_hours['fr_f']>20),1,0)

business_hours['weekend_dinner']=np.where(
    (business_hours['sa_s']< 15.5)&(business_hours['sa_f']>20)|
    (business_hours['su_s']< 15.5)&(business_hours['su_f']>20),1,0)

business_hours['weekday_late_night']=np.where(
    (business_hours['mo_s']< 23.5)&(business_hours['mo_f']<4)|
    (business_hours['tu_s']< 23.5)&(business_hours['tu_f']<4)|
    (business_hours['we_s']< 23.5)&(business_hours['we_f']<4)|
    (business_hours['th_s']< 23.5)&(business_hours['th_f']<4)|
    (business_hours['fr_s']< 23.5)&(business_hours['fr_f']<4),1,0)

business_hours['weekend_late_night']=np.where(
    (business_hours['sa_s']< 23.5)&(business_hours['sa_f']<4)|
    (business_hours['su_s']< 23.5)&(business_hours['su_f']<4),1,0)

business_hours

business_id  monday  tuesday  wednesday  thursday  friday  \
0       FYWN1wneV18bWNgQjJ2GNg       1        1          1         1       1   
1       He-G7vWjzVUysIKrfNbPUQ       1        1          1         1       1   
2       KQPW8lFf1y5BT2MxiSZ3QA       0        0          0         0       0   
3       8DShNS-LuFqpEWIp0HxijA       1        1          1         1       1   
4       PfOCPjBrlQAnz__NXj9h_w       1        1          1         1       1   
5       o9eMRCWt5PkpLDE0gOPtcQ       1        1          1         1       1   
6       kCoE3jvEtg6UVz5SOD3GVw       1        1          1         1       1   
7       OD2hnuuTJI9uotcKycxg1A       1        1          1         1       1   
8       EsMcGiZaQuG1OOvL9iUFug       0        0          0         0       0   
9       TGWhGNusxyMaA4kQVBNeew       1        1          1         1       1   
10      XOSRcvtaKc_Q5H1SAzN20A       0        0          0         0       0   
11      Y0eMNa5C-YU1RQOZf9XvVA       1        1          1         1       1   
12      xcgFnd-MwkZeO5G2HQ0gAQ       0        0          0         0       0   
13      NmZtoE3v8RdSJEczYbMT9g       1        1          1         1       1   
14      fNMVV_ZX7CJSDWQGdOM8Nw       1        1          1         1       1   
15      l09JfMeQ6ynYs5MCJtrcmQ       1        1          1         1       1   
16      IQSlT5jGE6CCDhSG0zG3xg       1        1          1         1       1   
17      b2I2DXtZVnpUMCXp1JON7A       1        1          1         1       1   
18      0FMKDOU8TJT1x87OKYGDTg       1        1          1         1       1   
19      Gu-xs3NIQTj3Mj2xYoN2aw       1        1          1         1       1   
20      lHYiCS-y8AFjUitv6MGpxg       1        1          1         1       1   
21      94KziT6DQ9XlBET3WzIv_w       0        0          0         0       0   
22      7YIy1tXOor9VCwvaSjuBHg       0        0          0         0       0   
23      PMH4oUa-bWELKogdtkWewg       1        1          1         1       1   
24      VSGcuYDV3q-AAZ9ZPq4fBQ       1        1          1         1       1   
25      1K4qrnfyzKzGgJPBEcJaNQ       1        1          1         1       1   
26      VBHEsoXQb2AQ76J9l8h1uQ       1        1          1         1       1   
27      AtdXq_gu9NTE5rx4ct_dGg       1        1          1         1       1   
28      Dj0S-Oe4ytRJzMGUPgYUkw       1        1          1         1       1   
29      gAy4LYpsScrj8POnCW6btQ       1        1          1         1       1   
30      nbhBRhZtdaZmMMeb2i02pg       1        1          1         1       1   
31      zzMu-6SmqhpvHxVRM6tx9g       1        1          1         1       1   
32      1_3nOM7s9WqnJWTNu2-i8Q       1        1          1         1       1   
33      FXHfcFVEfI1vVngW2gVOpw       1        1          1         1       1   
34      7gquCdaFoHZCcLYDttpHtw       1        1          1         1       1   
35      8y56fOiKhtCnqaiYB2S2Qg       0        0          0         0       0   
36      ok38fApaT1TBEU-IH85BvA       1        1          1         1       1   
37      lj0MiK5_fyv9df2twnsI7g       0        1          1         1       1   
38      S4a42azhoOmr0fpeNkggHg       0        0          0         0       0   
39      A_Ij4SwFmlRbVtRnsdSzWA       0        0          0         0       0   
40      tRVx2c89coruPRwYhGTcTw       1        1          1         1       1   
41      1Jp_hmPNUZArNqzpbm7B0g       1        1          1         1       1   
42      zjySmTfL9WiMDVgp8-Jp3w       0        0          0         0       0   
43      5qpi5VQ_S2Itm8xvRm1k8Q       1        1          1         1       1   
44      BnuzcebyB1AfxH0kjNWqSg       1        1          1         1       1   
45      rDMptJYWtnMhpQu_rRXHng       0        0          0         0       0   
46      1WBkAuQg81kokZIPMpn9Zg       1        1          1         1       1   
47      Z-4KHBDbdwyC7PwA_JE5Xw       1        1          1         1       1   
48      DPQnTnNw2PJj7DdENM98Cw       1        1          1         1       1   
49      _F3AMoo_zdl

In [70]:
bus_atts=business_attributes.drop(['AcceptsInsurance','HairSpecializesIn_coloring','HairSpecializesIn_africanamerican',
                                   'HairSpecializesIn_curly','HairSpecializesIn_perms','HairSpecializesIn_kids',
                                   'HairSpecializesIn_extensions','HairSpecializesIn_asian',
                                   'HairSpecializesIn_straightperms'],axis=1)

In [71]:
dfs = [business, bus_atts, business_hours] # list of dataframes

df_merged = reduce(lambda  left,right: pd.merge(left,right,on=['business_id'],
                                            how='left'), dfs)
df_merged=df_merged.drop(['neighborhood'],axis=1)
print(df_merged.shape)
df_merged.head(50)

(3318, 132)


business_id                                name  \
0   rDMptJYWtnMhpQu_rRXHng                        "McDonald's"   
1   1WBkAuQg81kokZIPMpn9Zg      "Charr An American Burger Bar"   
2   iPa__LOhse-hobC2Xmp-Kw                        "McDonald's"   
3   QkG3KUXwqZBW18A9k1xqCA                       "Red Lobster"   
4   5XejqzaFmtkZMstJS5Iy-w                       "D'Lish Cafe"   
5   2v-8QQfMLX2PCz-0S6gISQ                 "Papa John's Pizza"   
6   M3uV9Y3EDSpy9d4YwyNSAQ                         "Yakiramen"   
7   U1ZVgF-kfkvv_rcoe0RglQ                       "Pho Noodles"   
8   FfI9FOaQqzUxixw6_glt3Q                 "Affinito's Bistro"   
9   3b4efqz06QrLQ_w2xLc4pA   "Olive Garden Italian Restaurant"   
10  _eKvk2GoGKb3CoYolHgRlg    "Fresko A Mediterranean Kitchen"   
11  qB15WElGAlI_eGWjn0kT2w                         "Taco Bell"   
12  rSCevr5tQJTxPzMIq3n5Gw               "Yoshi's Asian Grill"   
13  to2cGMKdaw7ZHbXMzpfhlA          "Filiberto's Mexican Rest"   
14  X2oxkKB-wlu8xV0P8fbfiQ                      "Mo's Chicken"   
15  vhKUBKcOm8zOLxeS3XM9iA                    "Rosati's Pizza"   
16  frCxZS7lPhEnQRJ3UY6m7A                      "La Santisima"   
17  l0WauZ92kRg9bu2oxHj4TQ       "Aiello's East Coast Italian"   
18  Yar8jR2a1XA2JuRKfmNDcw                  "Palms Restaurant"   
19  qVQGfHphxolps16v6g5X-g     "Belfiore's Italian Ristorante"   
20  TolwZ3L28or4E8SVTZUf6Q                   "Spinato's Pizza"   
21  3w66rzZq_rjA1kSmVt5Hew                            "Subway"   
22  9KzLFQrA_tSBGVDNeZrB8Q      "Nick and Willy's Take & Bake"   
23  Ld2hhA3q3cdkptwS1fsYEg                      "Yogi's Grill"   
24  r0byBoB7y_IH8uicEvyCqQ                    "Rack Shack BBQ"   
25  BVYvfJiVcQTl9B311z518w                 "Peter Piper Pizza"   
26  aRRV_ZbRiD65SIi7vAY-iA                     "Zest of India"   
27  yX0pOWG_Be9TjGnm0aihVA                     "Modern  Grove"   
28  WaTXG26xbOGffSscvyr-wQ     "Spasso Pizza & Mozzarella Bar"   
29  ahfAFuFHO9tfFkoBIkVdmg        "Zabari Mediterranean Grill"   
30  kplbTXzOaUJqP2BwanoYjw                 "Dino's Ristorante"   
31  gKqzpzg2MmINROrgWqalOg           "Bill Johnsons Big Apple"   
32  Ndozr_--5-wzyDJ2T7TfpQ       "A & J Chicago Style Bar-B-Q"   
33  NihPkBRdA1AixuE_98tIrg                      "Port of Subs"   
34  RQdKieW9hqg898d_S2WwRA                       "Yogis Grill"   
35  cTJjTKz2huGZ-ElScC2pSw                           "Windsor"   
36  Q47FjaMLjI3v6yo-PHIebQ                         "Cafe Roma"   
37  tylsscXmLq03-DzGI36bIA                   "Squaw Peak Cafe"   
38  L7os7OGSQ2_evJRLvQg9dw                           "Wendy's"   
39  Lvr6DdVkFI8IMGfRvUcXQA              "Little Caesars Pizza"   
40  tvlHgHfBsmmNFbnFE06sgA                    "Sonic Drive-In"   
41  Lv2V5KqRlCl7_S6LKWkGlg                    "Devil's Greens"   
42  cOWXtCz7F9GQhPIks8gm6Q                    "SOLO Trattoria"   
43  7m1Oa1VYV98UUuo_6i0EZg    "Paradise Valley Burger Company"   
44  LcYrqMhUO_TITSXFk_SjJA                    "Sweet Tomatoes"   
45  iGvnkEz2efD9q-Z7ZcasWQ                 "Papa John's Pizza"   
46                  #NAME?                     "Panda Express"   
47  ZVtjS8Hvq2a6SxHxlehPGg        "L'Amore Italian Restaurant"   
48  sfGYIlU3ji6V3c0aWyny5A          "Lim's Chinese Restaurant"   
49  piHJq_NDrOh5SYk3AyQVOg  "Chestnut Fine Foods & Provisions"   

                                              address     city state  \
0                              "719 E Thunderbird Rd"  Phoenix    AZ   
1                     "777 E Thunderbird Rd, Ste 107"  Phoenix    AZ   
2                               "1635 E Camelback Rd"  Phoenix    AZ   
3                               "2810 North 75th Ave"  Phoenix    AZ   
4                                   "503 W Thomas Rd"  Phoenix    AZ   
5                               "3441 W Northern Ave"  Phoenix    AZ   
6                                  "10605 N 43rd Ave"  Phoenix    AZ   
7                                    "3417 N 7th Ave"  Phoenix    AZ   


In [72]:
df_merged.to_csv('/Users/Zeeshan/Downloads/business.csv',sep=',',index= False)

In [73]:
zipcodes = business.postal_code.unique().tolist()
len(zipcodes) # 41

48

In [74]:
demographics.count()
demographics.shape #(32977, 122)
demographics.head() #nulls might be non existant or they might be indicated with 0

# Create dataframe of demographics only with zip codes from business file
demographics_df=demographics[demographics.zcta.isin(zipcodes)]
demographics_df.shape #(41, 122) - matched all 41 zip codes

# Rename zip code column
demographics_df = demographics_df.rename(columns={'zcta': 'postal_code'})
demographics_df.count()

postal_code           41
primary_City          41
state                 41
primary_County        41
land_Area             41
water_Area            41
pop_2010              41
pop_2000              41
pop_Density           41
pop_Est_ACS           41
pop_Est_Factor        41
pop_Est_Level         41
poverty_Pct           41
group_Qtrs_Pct        41
college_Pct           41
degree_Pct            41
foreign_Pct           41
hH_Total              41
hH_Size               41
hH_Est                41
hH_Avg_Income         41
hH_Med_Income         41
hH_Earnings           41
hH_Earnings_Amt       41
hH_Retire             41
hH_Retire_Amt         41
hh_ss                 41
hH_SS_Amt             41
hh_ssi                41
hH_SSI_Amt            41
hH_Cash_Assist        41
hH_Cash_Assist_Amt    41
hH_Food_Stamps        41
family_Total          41
family_Size           41
family_Est            41
family_Avg_Income     41
family_Med_Income     41
per_Cap_Income        41
median_Age            41


In [75]:
business_df = pd.merge(df_merged,demographics_df,how='left',on='postal_code')

In [76]:
business_df

business_id                                    name  \
0     rDMptJYWtnMhpQu_rRXHng                            "McDonald's"   
1     1WBkAuQg81kokZIPMpn9Zg          "Charr An American Burger Bar"   
2     iPa__LOhse-hobC2Xmp-Kw                            "McDonald's"   
3     QkG3KUXwqZBW18A9k1xqCA                           "Red Lobster"   
4     5XejqzaFmtkZMstJS5Iy-w                           "D'Lish Cafe"   
5     2v-8QQfMLX2PCz-0S6gISQ                     "Papa John's Pizza"   
6     M3uV9Y3EDSpy9d4YwyNSAQ                             "Yakiramen"   
7     U1ZVgF-kfkvv_rcoe0RglQ                           "Pho Noodles"   
8     FfI9FOaQqzUxixw6_glt3Q                     "Affinito's Bistro"   
9     3b4efqz06QrLQ_w2xLc4pA       "Olive Garden Italian Restaurant"   
10    _eKvk2GoGKb3CoYolHgRlg        "Fresko A Mediterranean Kitchen"   
11    qB15WElGAlI_eGWjn0kT2w                             "Taco Bell"   
12    rSCevr5tQJTxPzMIq3n5Gw                   "Yoshi's Asian Grill"   
13    to2cGMKdaw7ZHbXMzpfhlA              "Filiberto's Mexican Rest"   
14    X2oxkKB-wlu8xV0P8fbfiQ                          "Mo's Chicken"   
15    vhKUBKcOm8zOLxeS3XM9iA                        "Rosati's Pizza"   
16    frCxZS7lPhEnQRJ3UY6m7A                          "La Santisima"   
17    l0WauZ92kRg9bu2oxHj4TQ           "Aiello's East Coast Italian"   
18    Yar8jR2a1XA2JuRKfmNDcw                      "Palms Restaurant"   
19    qVQGfHphxolps16v6g5X-g         "Belfiore's Italian Ristorante"   
20    TolwZ3L28or4E8SVTZUf6Q                       "Spinato's Pizza"   
21    3w66rzZq_rjA1kSmVt5Hew                                "Subway"   
22    9KzLFQrA_tSBGVDNeZrB8Q          "Nick and Willy's Take & Bake"   
23    Ld2hhA3q3cdkptwS1fsYEg                          "Yogi's Grill"   
24    r0byBoB7y_IH8uicEvyCqQ                        "Rack Shack BBQ"   
25    BVYvfJiVcQTl9B311z518w                     "Peter Piper Pizza"   
26    aRRV_ZbRiD65SIi7vAY-iA                         "Zest of India"   
27    yX0pOWG_Be9TjGnm0aihVA                         "Modern  Grove"   
28    WaTXG26xbOGffSscvyr-wQ         "Spasso Pizza & Mozzarella Bar"   
29    ahfAFuFHO9tfFkoBIkVdmg            "Zabari Mediterranean Grill"   
30    kplbTXzOaUJqP2BwanoYjw                     "Dino's Ristorante"   
31    gKqzpzg2MmINROrgWqalOg               "Bill Johnsons Big Apple"   
32    Ndozr_--5-wzyDJ2T7TfpQ           "A & J Chicago Style Bar-B-Q"   
33    NihPkBRdA1AixuE_98tIrg                          "Port of Subs"   
34    RQdKieW9hqg898d_S2WwRA                           "Yogis Grill"   
35    cTJjTKz2huGZ-ElScC2pSw                               "Windsor"   
36    Q47FjaMLjI3v6yo-PHIebQ                             "Cafe Roma"   
37    tylsscXmLq03-DzGI36bIA                       "Squaw Peak Cafe"   
38    L7os7OGSQ2_evJRLvQg9dw                               "Wendy's"   
39    Lvr6DdVkFI8IMGfRvUcXQA                  "Little Caesars Pizza"   
40    tvlHgHfBsmmNFbnFE06sgA                        "Sonic Drive-In"   
41    Lv2V5KqRlCl7_S6LKWkGlg                        "Devil's Greens"   
42    cOWXtCz7F9GQhPIks8gm6Q                        "SOLO Trattoria"   
43    7m1Oa1VYV98UUuo_6i0EZg        "Paradise Valley Burger Company"   
44    LcYrqMhUO_TITSXFk_SjJA                        "Sweet Tomatoes"   
45    iGvnkEz2efD9q-Z7ZcasWQ                     "Papa John's Pizza"   
46                    #NAME?                         "Panda Express"   
47    ZVtjS8Hvq2a6SxHxlehPGg            "L'Amore Italian Restaurant"   
48    sfGYIlU3ji6V3c0aWyny5A              "Lim's Chinese Restaurant"   
49    piHJq_NDrOh5SYk3AyQVOg      "Chestnut Fine Foods & Provisions"   
...                      ...                                     ...   
3268  LsaSrbOcV7M24Yc8nemdsA                             "Soma Cafe"   
3269  5xCeuEI7Einoi5xYsNuDCQ   "Applebee's Neighborhood Grill & Bar"   
3270  EFTYg_jOPf3abjWIPO92Cg                              "JT Gyros"   
3271  Jol7cXrDmKKmu_V6qp4wMA                             

In [77]:
business_df.to_csv('/Users/Zeeshan/Downloads/business.csv',sep=',',index= False)

# Standard Insights

In [114]:
import folium
from folium.plugins import MarkerCluster

m = folium.Map(location=[33.507070, -112.064382])
m

In [115]:
locations = business_df[['latitude', 'longitude']]
locationlist = locations.values.tolist()
len(locationlist)
locationlist[1:10]

[[33.60731, -112.063404],
 [33.508764899999996, -112.04624],
 [33.4787353, -112.2213794],
 [33.480301399999995, -112.0805864],
 [33.5528695, -112.1337118],
 [33.5823628, -112.1498845],
 [33.4887595, -112.08240179999999],
 [33.8649643, -112.1388202],
 [33.5803023, -112.1196529]]

In [116]:
map = folium.Map(location=[33.507070, -112.064382], zoom_start=12)
for point in range(0, len(locationlist)):
    folium.Marker(locationlist[point], popup=business_df['name'][point]).add_to(map)
map

In [117]:
map.save("my_map.html")

In [130]:
from folium.plugins import MarkerCluster
map2 = folium.Map(location=[33.507070, -112.064382], tiles='CartoDB dark_matter', zoom_start=11)

marker_cluster = MarkerCluster().add_to(map2)

for point in range(0, len(locationlist)):
    folium.Marker(locationlist[point], popup=business_df['name'][point]).add_to(marker_cluster)
map2

In [131]:
map2.save("my_map2.html")

In [125]:
folium_map = folium.Map(location=[33.507070, -112.064382],
                        zoom_start=11,
                        tiles="CartoDB dark_matter")
#marker = folium.CircleMarker(location=[40.738, -73.98])
for point in range(0, len(locationlist)):
    folium.CircleMarker(location=locationlist[point], popup=business_df['name'][point]).add_to(map)
marker.add_to(folium_map)

folium_map

In [126]:
folium_map.save("my_map3.html")